## 1. Scrape soccer tournaments from UOL web site

### 1.1 Create a scraping dataset by reading all Brazilian soccer A-league games (2012 to 2021) from CBF website

In [127]:
%%time
from urllib.request import Request, urlopen
from bs4 import BeautifulSoup as soup
import pandas as pd
import re

req = Request(url, headers={'User-Agent': 'Mozilla/5.0'})
html = urlopen(req).read()
page = soup(html, 'html.parser')
containers = page.findAll('div', class_ = 'swiper-wrapper')
tag = containers[0].text
df_final = pd.DataFrame(columns = ['Game', 'Year', 'Date', 'Time', 'Team1', 'Team2', 'Score1', 'Score2', 'Place'])

for year in range(2012, 2022):
    print(f'Reading data from {year}')
    url = 'https://www.cbf.com.br/futebol-brasileiro/competicoes/campeonato-brasileiro-serie-a/' + str(year)
    req = Request(url, headers={'User-Agent': 'Mozilla/5.0'})
    html = urlopen(req).read()
    page = soup(html, 'html.parser')
    containers = page.findAll('div', class_ = 'swiper-wrapper')
    tag = containers[0].text
    tag2 = re.sub(r'\d\salteração|\d\salterações', '', tag)
    tag2 = re.sub('Como foi o jogo|Detalhes do jogo|, ', '', tag2)
    year = url.split('/')[-1]
    pd.set_option("display.max_rows", None, "display.max_columns", 20)
    list_tag = re.split(r'Sáb|Dom|Seg|Ter|Qua|Qui|Sex', tag2)
    matches = []
    for line in list_tag:
        line = re.sub(r'\n|\r', ' ', line)
        line = re.sub(r'\s{2,}', '!', line)
        if line[0] != '!': matches.append(line.split(r'!'))
    df = pd.DataFrame(matches)
    df = df[[0, 2, 3, 4, 5, 6]]
    df.columns = ['DateTime', 'Game', 'Team1', 'Team2', 'Score', 'Place']
    df = df.drop(df.index[df['Team1'] == '(W.O. Duplo)'])   # delete WO matches that occured in 2016
    df = df.drop(df.index[df.Score.str.contains(':')])      # delete future matches in 2021
    df.Score = df.Score.replace('\(|-|\)|', '', regex=True)  # eliminate (-) from score in 2014
    df['Year'] = year
    df['Game'] = df['Game'].apply(lambda x:x.split('Jogo: ')[1])
    df['Score1'] = df['Score'].apply(lambda x:x.split(' x ')[0])
    df['Score2'] = df['Score'].apply(lambda x:x.split(' x ')[1])
    df[['Date', 'Time']] = df['DateTime'].str.split(' ', 1, expand=True)
    df[['Stadium', 'City', 'Stadium']] = df['Place'].str.split(' - ', 2, expand=True)
    df['Score1'] = pd.to_numeric(df['Score1'])
    df['Score2'] = pd.to_numeric(df['Score2'])
    df.reset_index(inplace=True)
    for i in range(len(df)):
        if df.loc[i, 'Score1'] > df.loc[i, 'Score2']:
            df.loc[i, 'Winner'] = df.loc[i, 'Team1']
            df.loc[i, 'Loser'] = df.loc[i, 'Team2']
        if df.loc[i, 'Score1'] < df.loc[i, 'Score2']:
            df.loc[i, 'Winner'] = df.loc[i, 'Team2']
            df.loc[i, 'Loser'] = df.loc[i, 'Team1']
        if df.loc[i, 'Score1'] == df.loc[i, 'Score2']:
            df.loc[i, 'Tie1'] = df.loc[i, 'Team1']
            df.loc[i, 'Tie2'] = df.loc[i, 'Team2']
        df.loc[i, 'TotalGoals'] = df.loc[i, 'Score1'] + df.loc[i, 'Score2'].astype('int')
        df.loc[i, 'DifGoals'] = abs(df.loc[i, 'Score1'] - df.loc[i, 'Score2']).astype('int')
    df_final = df_final.append(df, ignore_index=True)
print('Data is now ready')
df_final

Reading data from 2012
Reading data from 2013
Reading data from 2014
Reading data from 2015
Reading data from 2016
Reading data from 2017
Reading data from 2018
Reading data from 2019
Reading data from 2020
Reading data from 2021
Data is now ready
Wall time: 50.1 s


Game  Year        Date   Time Team1 Team2 Score1 Score2  \
0       3  2012  19/05/2012  18:30   PAL   POR      1      1   
1      10  2012  19/05/2012  18:30   SPO   FLA      1      1   
2       4  2012  19/05/2012  21:00   FIG   NAU      2      1   
3       8  2012  20/05/2012  16:00   PON   ATL      0      1   
4       5  2012  20/05/2012  16:00   COR   FLU      0      1   
5       7  2012  20/05/2012  16:00   BOT   SAO      4      2   
6       6  2012  20/05/2012  16:00   INT   COR      2      0   
7       1  2012  20/05/2012  18:30   VAS   GRE      2      1   
8       2  2012  20/05/2012  18:30   BAH   SAN      0      0   
9       9  2012  20/05/2012  18:30   CRU   ATL      0      0   
10     11  2012  26/05/2012  18:30   ATL   PON      1      1   
11     12  2012  26/05/2012  18:30   FLA   INT      3      3   
12     13  2012  26/05/2012  18:30   POR   VAS      0      1   
13     14  2012  26/05/2012  21:00   NAU   CRU      0      0   
14     18  2012  27/05/2012  16:00   SAN   SPO      0      0   
15     16  2012  27/05/2012  16:00   ATL   COR      1      0   
16     17  2012  27/05/2012  16:00   COR   BOT      2      3   
17     15  2012  27/05/2012  16:00   SAO   BAH      1      0   
18     19  2012  27/05/2012  18:30   GRE   PAL      1      0   
19     20  2012  27/05/2012  18:30   FLU   FIG      2      2   
20     21  2012  06/06/2012  19:30   ATL   GRE      0      1   
21     22  2012  06/06/2012  19:30   SPO   PAL      2      1   
22     23  2012  06/06/2012  20:30   VAS   NAU      4      2   
23     24  2012  06/06/2012  20:30   ATL   BAH      1      1   
24     25  2012  06/06/2012  20:30   COR   POR      2      0   
25     28  2012  06/06/2012  21:50   PON   FLA      2      2   
26     26  2012  06/06/2012  21:50   INT   SAO      1      0   
27     27  2012  06/06/2012  21:50   SAN   FLU      1      1   
28     29  2012  07/06/2012  21:00   COR   FIG      1      1   
29     30  2012  07/06/2012  21:00   BOT   CRU      2      3   
30     32  2012  09/06/2012  18:30   FLA   COR      3      1   
31     33  2012  09/06/2012  21:00   PAL   ATL      0      1   
32     31  2012  10/06/2012  16:00   POR   ATL      2      0   
33     34  2012  10/06/2012  17:00   GRE   COR      2      0   
34     35  2012  10/06/2012  17:00   FLU   INT      0      0   
35     36  2012  10/06/2012  17:00   BAH   VAS      1      2   
36     40  2012  10/06/2012  18:30   NAU   BOT      3      2   
37     38  2012  10/06/2012  18:30   FIG   PON      0      0   
38     39  2012  10/06/2012  18:30   CRU   SPO      1      0   
39     37  2012  10/06/2012  18:30   SAO   SAN      1      0   
40     43  2012  16/06/2012  18:30   INT   BOT      1      2   
41     44  2012  16/06/2012  18:30   CRU   FIG      1      0   
42     41  2012  16/06/2012  21:00   FLU   POR      4      1   
43     42  2012  17/06/2012  16:00   SAO   ATL      1      0   
44     45  2012  17/06/2012  16:00   PAL   VAS      1      1   
45     47  2012  17/06/2012  16:00   BAH   SPO      2      1   
46     49  2012  17/06/2012  16:00   FLA   SAN      1      0   
47     50  2012  17/06/2012  18:30   NAU   GRE      1      0   
48     48  2012  17/06/2012  18:30   COR   ATL      3      0   
49     46  2012  17/06/2012  18:30   PON   COR      1      0   
50     52  2012  23/06/2012  18:30   VAS   CRU      1      3   
51     53  2012  23/06/2012  18:30   POR   SAO      1      0   
52     51  2012  23/06/2012  21:00   ATL   NAU      5      1   
53     55  2012  24/06/2012  16:00   COR   PAL      2      1   
54     56  2012  24/06/2012  16:00   GRE   FLA      2      0   
55     57  2012  24/06/2012  16:00   FIG   BAH      1      1   
56     54  2012  24/06/2012  18:30   SPO   INT      0      2   
57     58  2012  24/06/2012  18:30   BOT   PON      1      2   
58     59  2012  24/06/2012  18:30   SAN   COR      2      2   
59     60  2012  24/06/2012  18:30   ATL   FLU      1      4   
60     64  2012  30/06/2012  16:20   NAU   FLU      0      2   
61     62  2012  30/06/2012  16:20   

In [135]:
df.to_excel('soccer_stats.xlsx')

In [ ]:
df[df.index[]]

In [133]:
a = list(df.Winner)
a.append(list(df.Loser))
a

[nan,
 'BAH',
 nan,
 'FOR',
 'FLA',
 'CEA',
 'RED',
 'ATL',
 'ATH',
 nan,
 'ATL',
 nan,
 'SAN',
 'FLU',
 'COR',
 'FOR',
 'PAL',
 'ATH',
 'ATL',
 nan,
 nan,
 'FLA',
 'ATL',
 'ATH',
 nan,
 nan,
 'INT',
 'FOR',
 'CUI',
 nan,
 'ATL',
 'RED',
 'PAL',
 'BAH',
 nan,
 nan,
 'FLU',
 'SPO',
 nan,
 'RED',
 'PAL',
 nan,
 nan,
 'ATH',
 'SAN',
 nan,
 'JUV',
 nan,
 'GRE',
 'FLA',
 nan,
 'RED',
 'ATL',
 nan,
 'COR',
 'CEA',
 'INT',
 nan,
 'BAH',
 'JUV',
 nan,
 nan,
 'PAL',
 nan,
 nan,
 'SAN',
 nan,
 nan,
 'RED',
 'FOR',
 'ATH',
 'AME',
 'PAL',
 nan,
 nan,
 'JUV',
 nan,
 'ATL',
 'FLA',
 'AME',
 'ATH',
 nan,
 'BAH',
 'PAL',
 'FLU',
 'RED',
 'CEA',
 'ATL',
 'ATL',
 'SAN',
 nan,
 'BAH',
 'FOR',
 'PAL',
 'ATL',
 nan,
 nan,
 'SAO',
 'COR',
 'PAL',
 nan,
 nan,
 'SAO',
 'ATL',
 'FLU',
 nan,
 'FLA',
 nan,
 'FOR',
 'CEA',
 'FOR',
 'ATL',
 'GRE',
 'CUI',
 'PAL',
 'FLA',
 'INT',
 nan,
 'SPO',
 nan,
 'PAL',
 'ATL',
 'FOR',
 'FLA',
 'ATH',
 'ATL',
 nan,
 'JUV',
 'COR',
 nan,
 nan,
 'RED',
 'FLA',
 'ATL',
 'SAN',
 '

In [ ]:
df

In [122]:
df2 = df.copy()
df2.iloc[299]

DateTime                22/10/2014 22:30
Game                                 292
Team1                                SPO
Team2                                GOI
Score                           (-)0 x 1
Place       Ilha do Retiro - Recife - PE
Year                                2014
Score1                              (-)0
Score2                                 1
Date                          22/10/2014
Time                               22:30
Stadium                               PE
City                              Recife
Name: 299, dtype: object

In [123]:
df2.Score = df2.Score.replace('\(|-|\)|', '', regex=True)
df2.iloc[299]

DateTime                22/10/2014 22:30
Game                                 292
Team1                                SPO
Team2                                GOI
Score                              0 x 1
Place       Ilha do Retiro - Recife - PE
Year                                2014
Score1                              (-)0
Score2                                 1
Date                          22/10/2014
Time                               22:30
Stadium                               PE
City                              Recife
Name: 299, dtype: object

In [97]:
re.sub("(-)","", df2['Score'].str)
#df[298:301]

TypeError: expected string or bytes-like object

In [87]:
matches[298:301]

[['22/10/2014 22:00',
  '-',
  'Jogo: 300',
  'CHA',
  'SAO',
  '0 x 0',
  'Arena Condá - Chapeco - SC',
  ''],
 ['22/10/2014 22:30',
  '-',
  'Jogo: 292',
  'SPO',
  'GOI',
  '(-)0 x 1',
  'Ilha do Retiro - Recife - PE',
  'Rodada 31',
  ''],
 ['25/10/2014 16:20',
  '-',
  'Jogo: 304',
  'PAL',
  'COR',
  '1 x 1',
  'Pacaembu - Sao Paulo - SP',
  '']]

In [88]:
tag

'\n\n\nRodada 1\n\n\n\n\n\n\n\n\r\n                              Sáb, 19/04/2014 18:30\r\n                            -  Jogo: 2 \r\n                          \n\n\n\nFLU\n\n\n\nFIG\n\n\n\n3 x 0\n\n\n\n\r\n              Maracanã - Rio de Janeiro - RJ\nComo foi o jogo\n\n\n\n\n\n\r\n                              Sáb, 19/04/2014 18:30\r\n                            -  Jogo: 8 \r\n                          \n\n\n\nINT\n\n\n\nVIT\n\n\n\n1 x 0\n\n\n\n\r\n              Beira-Rio - Porto Alegre - RS\nComo foi o jogo\n\n\n\n\n\n\r\n                              Sáb, 19/04/2014 21:00\r\n                            -  Jogo: 10 \r\n                          \n\n\n\nCHA\n\n\n\nCOR\n\n\n\n0 x 0\n\n\n\n\r\n              Arena Condá - Chapeco - SC\nComo foi o jogo\n\n\n\n\n\n\r\n                              Dom, 20/04/2014 16:00\r\n                            -  Jogo: 3 \r\n                          \n\n\n\nSAO\n\n\n\nBOT\n\n\n\n3 x 0\n\n\n\n\r\n              Morumbi - Sao Paulo - SP\nComo foi o jog

In [79]:
df['Score1'] = pd.to_numeric(df['Score1'])
df['Score2'] = pd.to_numeric(df['Score2'])
for i in range(len(df)):
    if df.loc[i, 'Score1'] > df.loc[i, 'Score2']:
        df.loc[i, 'Winner'] = df.loc[i, 'Team1']
        df.loc[i, 'Loser'] = df.loc[i, 'Team2']
    if df.loc[i, 'Score1'] < df.loc[i, 'Score2']:
        df.loc[i, 'Winner'] = df.loc[i, 'Team2']
        df.loc[i, 'Loser'] = df.loc[i, 'Team1']
    if df.loc[i, 'Score1'] == df.loc[i, 'Score2']:
        df.loc[i, 'Tie1'] = df.loc[i, 'Team1']
        df.loc[i, 'Tie2'] = df.loc[i, 'Team2']
    df.loc[i, 'TotalGoals'] = df.loc[i, 'Score1'] + df.loc[i, 'Score2']
    df.loc[i, 'DifGoals'] = abs(df.loc[i, 'Score1'] - df.loc[i, 'Score2'])
#df['Score2'] = int(df['Score2'])

df.head()

index          DateTime Game Team1 Team2  Score  \
0      0  29/05/2021 19:00   10   CUI   JUV  2 x 2   
1      1  29/05/2021 20:00    7   BAH   SAN  3 x 0   
2      2  29/05/2021 21:00    3   SAO   FLU  0 x 0   
3      3  30/05/2021 11:00    4   ATL   FOR  1 x 2   
4      4  30/05/2021 16:00    1   FLA   PAL  1 x 0   

                            Place  Year  Score1  Score2        Date   Time  \
0    Arena Pantanal - Cuiaba - MT  2021       2       2  29/05/2021  19:00   
1         Pituaçu - Salvador - BA  2021       3       0  29/05/2021  20:00   
2        Morumbi - Sao Paulo - SP  2021       0       0  29/05/2021  21:00   
3  Mineirão - Belo Horizonte - MG  2021       1       2  30/05/2021  11:00   
4  Maracanã - Rio de Janeiro - RJ  2021       1       0  30/05/2021  16:00   

  Stadium            City Tie1 Tie2  TotalGoals  DifGoals Winner Loser  
0      MT          Cuiaba  CUI  JUV         4.0       0.0    NaN   NaN  
1      BA        Salvador  NaN  NaN         3.0       3.0    BAH   SAN  
2      SP       Sao Paulo  SAO  FLU         0.0       0.0    NaN   NaN  
3      MG  Belo Horizonte  NaN  NaN         3.0       1.0    FOR   ATL  
4      RJ  Rio de Janeiro  NaN  NaN         1.0       1.0    FLA   PAL

In [74]:
i

19

In [76]:
df.iloc[i]

DateTime                     12/06/2021 19:00
Game                                       22
Team1                                     PAL
Team2                                     COR
Score                                   1 x 1
Place         Allianz Parque - Sao Paulo - SP
Year                                     2021
Score1                                      1
Score2                                      1
Date                               12/06/2021
Time                                    19:00
Stadium                                    SP
City                                Sao Paulo
Tie1                                      NaN
Tie2                                      NaN
TotalGoals                                NaN
DifGoals                                  NaN
Winner                                    NaN
Loser                                     NaN
Name: 20, dtype: object

In [77]:
df

DateTime Game Team1 Team2  Score  \
0    29/05/2021 19:00   10   CUI   JUV  2 x 2   
1    29/05/2021 20:00    7   BAH   SAN  3 x 0   
2    29/05/2021 21:00    3   SAO   FLU  0 x 0   
3    30/05/2021 11:00    4   ATL   FOR  1 x 2   
4    30/05/2021 16:00    1   FLA   PAL  1 x 0   
5    30/05/2021 16:00    6   CEA   GRE  3 x 2   
6    30/05/2021 18:15    9   CHA   RED  0 x 3   
7    30/05/2021 18:15    2   COR   ATL  0 x 1   
8    30/05/2021 18:15    8   ATH   AME  1 x 0   
9    30/05/2021 20:30    5   INT   SPO  2 x 2   
10   05/06/2021 19:00   20   ATL   SAO  2 x 0   
11   05/06/2021 21:00   18   RED   BAH  3 x 3   
12   05/06/2021 21:00   13   SAN   CEA  3 x 1   
13   06/06/2021 11:00   11   FLU   CUI  1 x 0   
14   06/06/2021 16:00   14   AME   COR  0 x 1   
15   06/06/2021 16:00   16   FOR   INT  5 x 1   
16   06/06/2021 18:15   12   PAL   CHA  3 x 1   
17   06/06/2021 18:15   19   JUV   ATH  0 x 3   
18   06/06/2021 20:30   17   SPO   ATL  0 x 1   
20   12/06/2021 19:00   22   PAL   COR  1 x 1   
21   12/06/2021 19:00   23   SAN   JUV  0 x 0   
22   13/06/2021 16:00   21   FLA   AME  2 x 0   
23   13/06/2021 16:00   24   ATL   SAO  1 x 0   
24   13/06/2021 16:00   25   GRE   ATH  0 x 1   
25   13/06/2021 20:30   28   RED   FLU  2 x 2   
26   13/06/2021 20:30   29   CHA   CEA  0 x 0   
27   13/06/2021 20:30   27   BAH   INT  0 x 1   
28   13/06/2021 20:30   26   FOR   SPO  1 x 0   
29   21/07/2021 19:00   30   CUI   ATL  2 x 1   
30   16/06/2021 19:00   33   SAO   CHA  1 x 1   
31   16/06/2021 19:00   35   INT   ATL  0 x 1   
32   16/06/2021 20:30   32   COR   RED  1 x 2   
33   16/06/2021 21:30   39   JUV   PAL  0 x 3   
34   17/06/2021 16:00   36   CEA   BAH  1 x 2   
35   17/06/2021 16:00   34   AME   CUI  0 x 0   
36   17/06/2021 19:00   40   ATL   FOR  0 x 0   
37   17/06/2021 19:00   31   FLU   SAN  1 x 0   
38   17/06/2021 19:00   37   SPO   GRE  1 x 0   
39   02/11/2021 16:00   38   ATH   FLA  2 x 2   
40   19/06/2021 21:00   41   FLA   RED  2 x 3   
41   20/06/2021 11:00   42   PAL   AME  2 x 1   
42   20/06/2021 16:00   45   INT   CEA  1 x 1   
43   20/06/2021 16:00   47   BAH   COR  0 x 0   
44   20/06/2021 18:15   48   ATH   ATL  2 x 1   
45   20/06/2021 18:15   43   SAN   SAO  2 x 0   
46   20/06/2021 18:15   46   FOR   FLU  1 x 1   
47   20/06/2021 20:30   49   JUV   SPO  1 x 0   
48   21/06/2021 20:00   44   ATL   CHA  1 x 1   
49   18/08/2021 19:00   50   CUI   GRE  0 x 1   
50   23/06/2021 19:00   51   FLA   FOR  2 x 1   
51   23/06/2021 19:00   53   SAO   CUI  2 x 2   
52   23/06/2021 19:00   58   RED   PAL  3 x 1   
53   23/06/2021 19:00   60   ATL   FLU  1 x 0   
54   24/06/2021 16:00   54   AME   JUV  1 x 1   
55   24/06/2021 19:00   52   COR   SPO  2 x 1   
56   24/06/2021 19:00   56   CEA   ATL  2 x 1   
57   24/06/2021 19:00   59   CHA   INT  1 x 2   
58   24/06/2021 21:30   55   GRE   SAN  2 x 2   
59   24/06/2021 21:30   57   BAH   ATH  2 x 1   
60   27/06/2021 11:00   69   JUV   FLA  1 x 0   
61   27/06/2021 16:00   61   FLU   COR  1 x 1   
62   27/06/2021 20:00   65   GRE   FOR  0 x 0   
63   27/06/2021 20:00   62   PAL   BAH  3 x 2   
64   27/06/2021 20:00   68   ATH   CHA  2 x 2   
65   27/06/2021 20:30   64   AME   INT  1 x 1   
66   27/06/2021 20:30   63   SAN   ATL  2 x 0   
67   27/06/2021 20:30   66   CEA   SAO  1 x 1   
68   27/06/2021 20:30   67   SPO   CUI  0 x 0   
69   28/06/2021 20:00   70   ATL   RED  0 x 1   
70   30/06/2021 16:00   76   FOR   CHA  3 x 2   
71   30/06/2021 16:00   71   FLU   ATH  1 x 4   
72   30/06/2021 19:00   77   BAH   AME  3 x 4   
73   30/06/2021 19:00   75   INT   PAL  1 x 2   
74   30/06/2021 20:30   73   SAN   SPO  0 x 0   
75   30/06/2021 21:30   72   COR   SAO  0 x 0   
76   30/06/2021 21:30   79   JUV   GRE  2 x 0   
77   01/07/2021 16:00   78   RED   CEA  0 x 0   
78   01/07/2021 19:00   74   ATL   ATL  4 x 1   
79   01/07/2021 20:00   80   CUI   FLA  0 x 2   
80   03/07/2021 19:00   84   AME   SAN  2 x 0   
81   03/07/2021 19:00   88   ATH   FOR  2 x 

In [ ]:
if re.search('encerrado           A definir', tag) != None:
    part1, part2 = re.split('encerrado           A definir', tag)[:2]
    part2_split = re.split('A definir', part2)
    part3 = []
    for part in part2_split:
        part = part.split('  ')
        part = part[2] + ' - * - * - ' + part[1]
        part3.append(part)
    part2 = "            ".join(part3)
    tag = part1 + part2
    tag
tag = re.sub('Domus', 'DOMUS', tag)
games = re.split('Sáb|Dom|Seg|Ter|Qua|Qui|Sex|pós-jogo', tag)
games = [g.replace(',', ' ').strip() for g in games if g.strip() != '']

for i in range(len(games)):
    res1 = re.search(r'^\d\d/\d\d\s-\s\d\dh\d*', games[i])
    if i<len(games)-1: res2 = re.search(r'^\d\d/\d\d\s-\s\d\dh\d*', games[i+1])
    if res1 == None and res2 != None: 
        games[i] = res2[0] + ' - ' + games[i]
games = [re.sub(r'\s{3,9}', ' - ', g).strip() for g in games if len(g.split('-')) > 2]
games = [re.split(r' - |\(\)', g) for g in games]
df = pd.DataFrame(games).iloc[:,:5]
df.columns = ['Date', 'Time', 'Place', 'Team1', 'Team2']
df[['Score1', 'Score2']] = ''

for i in range(len(df)):
    txt1 = df.loc[i,'Team1'].strip()[3:]
    score1 = re.findall(r'\d$|-$', txt1)[0]
    if score1== '-': score1=''
    txt2 = df.loc[i,'Team2'].strip()[:-3]
    score2 = re.findall(r'^\d+|^-', txt2)[0]
    if score2== '-': score2=''
    df.loc[i, 'Team1'] = re.split(r'\d+|-$', txt1)[0]
    df.loc[i, 'Team2'] = re.split(r'^\d+|^-', txt2)[1]
    df.loc[i, 'Score1'] = score1
    df.loc[i, 'Score2'] = score2
df.replace('*', '', inplace=True)

### 1.2 Create a scraping dataset with the ranking of soccer double-round-robin tournaments

In [ ]:
def uol_ranking(url):
    page = pd.read_html(url)
    df = pd.concat([pd.DataFrame(page[0]), pd.DataFrame(page[1])], axis=1)
    df.rename(columns = {'classificação':'Ranking'}, inplace = True)
    df[['Ranking', 'Team']] = df['Ranking'].str.split('°', 1, expand=True)
    df['Team'] = df['Team'].apply(lambda x:re.split(r'[A-Z]{3}$', x)[0].strip())
    cols = df.columns.tolist()
    cols = [cols[0], cols[-1]] + cols[1:-1]
    df = df[cols]
    return df

### 1.3 Show part of dataset with soccer matches and ranking of different leagues

In [ ]:
leagues = ['https://www.uol.com.br/esporte/futebol/campeonatos/brasileirao',
           'https://www.uol.com.br/esporte/futebol/campeonatos/serie-b',
           'https://www.uol.com.br/esporte/futebol/campeonatos/eliminatorias-sul-americanas',
           'https://www.uol.com.br/esporte/futebol/campeonatos/frances',
           'https://www.uol.com.br/esporte/futebol/campeonatos/alemao',
           'https://www.uol.com.br/esporte/futebol/campeonatos/la-liga',
           'https://www.uol.com.br/esporte/futebol/campeonatos/italiano',
           'https://www.uol.com.br/esporte/futebol/campeonatos/ingles']

for league in leagues:
    print('League:', league.split('/')[-1].capitalize())
    display(uol_ranking(league).head(4))
    display(uol_matches(league).head(4))
    print('')